In [1]:
import scrapy
import numpy as np
from scrapy.crawler import CrawlerProcess
import re
import json

In [2]:
class Diputados(scrapy.Spider):
    name = "spider_diputados"
    
    def start_requests(self):
        links = [urlCurr + i for i in terminaciones]
        for link in links:
            yield scrapy.Request( url = link, headers={'User-Agent': 'Mozilla/5.0 (X11; Ubuntu; Linux x86_64; rv:66.0) Gecko/20100101 Firefox/66.0'}, 
                              callback = self.parse )
    
    def parse(self,response):
        nombre = response.css('td.textocurrienc > center > strong::text').get()
        nombre = limpiaText(nombre) # cambié esto
        idDipu = ''.join([c for c in nombre[1:] if c.isupper()])
        cumple = response.css('td.textocurri:nth-of-type(2) > strong::text').extract()[6]
        curp = creaCurp(nombre,cumple)
        dipus[curp]={}
        dipus.get(curp,{})['CURP']=curp # Agregué esto para 
        dipus.get(curp,{})['Nombre']=nombre # cambié aquí
        dipus.get(curp,{})['TipoElección']=response.css('td.textocurri:nth-of-type(2) > strong::text').extract_first()
        dipus.get(curp,{})['Entidad']=response.css('td.textocurri:nth-of-type(2) > strong::text').extract()[1]
        parti=response.xpath('//table[@class="cajasombra"]//img/@src').extract()[1]
        dipus.get(curp,{})['Partido']=obtienePartido(parti)
        distri1 =response.css('td.textocurri:nth-of-type(2) > strong::text').extract()[2]
        distri2 =response.css('td.textocurri:nth-of-type(2) > strong::text').extract()[3]  # PARTE RARA
        dipus.get(curp,{})['Distrito'] = distri1 +""+ distri2
        dipus.get(curp,{})['Correo']=response.css('td.textocurri:nth-of-type(2) > strong::text').extract()[4]
        dipus.get(curp,{})['Extensión']=response.css('td.textocurri:nth-of-type(2) > strong::text').extract()[5]
        dipus.get(curp,{})['Onomástico']=cumple
        supl=response.css('td.textocurri:nth-of-type(2)::text').extract()[6]
        dipus.get(curp,{})['Suplente']=limpiaText(supl)
        dipus.get(curp,{})['Comisiones']=response.xpath('//a[contains(@href, "integrantes_de_comision")]/text()').getall()
        dipus.get(curp,{})['Último grado de estudios']=response.xpath('//td[@class="textoNegro"]/text()').extract_first()
        link_asis=urlDipu + response.css('table.tableInfo  a::attr(href)').extract()[0]
        link_votaciones=urlDipu + response.css('table.tableInfo  a::attr(href)').extract()[1]
        yield response.follow(url=link_asis, headers={'User-Agent': 'Mozilla/5.0 (X11; Ubuntu; Linux x86_64; rv:66.0) Gecko/20100101 Firefox/66.0'},meta={'curp':curp},
                              callback=self.parse2)
        yield response.follow(url=link_votaciones, headers={'User-Agent': 'Mozilla/5.0 (X11; Ubuntu; Linux x86_64; rv:66.0) Gecko/20100101 Firefox/66.0'},meta={'curp':curp},
                              callback=self.parse4)
    
    def parse2(self,response):
        curp = response.meta['curp']
        referencias = response.xpath('//a[@class="linkVerde"]/@href').extract()
        links = [urlDipu + referencia for referencia in referencias]
        for li in links:
            yield response.follow(url=li, headers={'User-Agent': 'Mozilla/5.0 (X11; Ubuntu; Linux x86_64; rv:66.0) Gecko/20100101 Firefox/66.0'},meta={'curp':curp},
                              callback=self.parse3)
    
    def parse3(self,response):
        curp = response.meta['curp']
        prueba = response.xpath('//tr/td/div/font/text()').extract()
        dias = list(filter(lambda a: (a == 'A' or a =='AC'), prueba))
        dipus.get(curp,{})['Asistencias']=dipus.get(curp,{}).get('Asistencias',0) + len(dias)

    def parse4(self,response):
        curp = response.meta['curp']
        referencias = response.xpath('//a[@class="linkVerde"]/@href').extract()
        links = [urlDipu + referencia for referencia in referencias]
        for li in links:
            yield response.follow(url=li, headers={'User-Agent': 'Mozilla/5.0 (X11; Ubuntu; Linux x86_64; rv:66.0) Gecko/20100101 Firefox/66.0'},meta={'curp':curp},
                              callback=self.parse5)
                
    def parse5(self,response):
        curp = response.meta['curp']
        aux = response.xpath('//td[@class="smallVerde"]/text()').extract()
        aux2={}
        for i in range(1,len(aux),4):
            votos = {}
            votacion = response.xpath('//td[@class="smallVerde"]/text()').extract()[i]
            posi = response.xpath('//td[@class="smallVerde"]/text()').extract()[i+2]
            if(votacion in por_votaciones.keys()):
                por_votaciones[votacion][curp]=posi
            else:
                    por_votaciones[votacion] = {"ID_voto":limpiaVotacion(votacion),"Nombre_Votación":votacion, curp:posi}
            votos['votación']=votacion
            votos['posición']=posi
            aux2['votos']=aux2.get('votos', []) + [votos]
            #dipus.get(curp,{})['votos']=dipus.get(curp,{}).get('votos', []) + [votos]
        dipus.get(curp,{})['votos']=dipus.get(curp,{}).get('votos',0)+len(aux2.get('votos', [])) # Se comenta si la de arriba se descomenta


        

In [3]:
def creaCurp(nombre,cumple):
    
    '''
    iniciales = ''.join([c for c in nombre[1:] if c.isupper()])
    c = cumple.replace('-', ' ').split(' ')
    if(len(c[0])==1):
        c[0]="0"+c[0] 
    curp = iniciales[0:3]+c[0]+c[1][0:3]+c[2][-2:]
    '''
    curp = nombre.replace(' ', '')
    curp = curp.upper()
    curp = curp.replace('Á', 'A')
    curp = curp.replace('É', 'E')
    curp = curp.replace('Í', 'I')
    curp = curp.replace('Ó', 'O')
    curp = curp.replace('Ú', 'U')
    curp = curp.replace('Ñ', 'N')
    return curp

In [4]:
def limpiaText(nom):
    resp = re.sub('\s+',' ',nom)
    resp = resp.replace('Dip. ', '')
    resp = resp.replace('(LICENCIA)', '')
    resp = resp.replace('Suplente: ', '')
    resp = resp.replace('(DECESO)', '')
    resp = resp.replace('(Deceso)', '')
    resp = resp.replace('  ', ' ')
    if(resp[-1]==" "):
        resp = resp[0:len(resp)-1]
    if(resp[0]==" "):
        resp = resp[1:]
    return resp

In [5]:
def limpiaVotacion(nombreVot):
    nombreVot = nombreVot.replace('(', '')
    nombreVot = nombreVot.replace(')', '')
    nombreVot = nombreVot.replace(' SE ', ' ')
    nombreVot = nombreVot.replace('DECRETO', '')
    nombreVot = nombreVot.replace(' QUE ', ' ')
    nombreVot = nombreVot.replace(' SE ', ' ')
    nombreVot = nombreVot.replace(' DE ', ' ')
    nombreVot = nombreVot.replace(' A ', ' ')
    nombreVot = nombreVot.replace(' LA ', ' ')
    nombreVot = nombreVot.replace(' EL ', ' ')
    nombreVot = nombreVot.replace(' POR ', ' ')
    nombreVot = nombreVot.replace(' PARA ', ' ')
    nombreVot = nombreVot.replace(' LOS ', ' ')
    nombreVot = nombreVot.replace(' LAS ', ' ')
    nombreVot = nombreVot.replace(' Y ', ' ')
    nombreVot = nombreVot.replace(' E ', ' ')
    nombreVot = nombreVot.replace(' CON ', ' ')
    nombreVot = nombreVot.replace(' LEY ', ' ')
    nombreVot = nombreVot.replace(' EN ', ' ')
    nombreVot = nombreVot.replace(' LO ', ' ')
    nombreVot = nombreVot.replace(' DEL ', ' ')
    nombreVot = nombreVot.replace('.', ' ')
    nombreVot = nombreVot.replace(';', ' ')
    nombreVot = nombreVot.replace(',', ' ')
    nombreVot = nombreVot.replace('  ', ' ')
    nombreFin=""
    for s in nombreVot.split():
        nombreFin+=s[0]
    return nombreFin
    

In [6]:
def obtienePartido(imagen):
    res=""
    if(imagen=='images/pan.png'):
        res = "PAN"
    elif(imagen=='images/Logo_PT.png'):
        res = "PT"
    elif(imagen=='images/LogoMorena.jpg'):
        res = "Morena"
    elif(imagen=='images/encuentro.png'):
        res = "Encuentro Social"
    elif(imagen=='images/logo_movimiento_ciudadano.png'):
        res = "Movimiento Ciudadano"
    elif(imagen=='images/pri01.png'):
        res = "PRI"
    elif(imagen=='images/logvrd.jpg'):
        res = "Partido Verde"
    elif(imagen=='images/prd01.png'):
        res = "PRD"
    elif(imagen=='images/logo_SP.jpg'):
         res = "Sin Partido"
    else:
         res = imagen
    return res
                                    

In [7]:
dipus={}
curp = "h"
urlDipu = "http://sitl.diputados.gob.mx/LXIV_leg/"
urlCurr = "http://sitl.diputados.gob.mx/LXIV_leg/curricula.php?dipt="

por_votaciones = {}

terminaciones = []
for i in range(0,5):
    for j in range(0,10):
        for k in range(0,10):
            terminaciones.append(str(i)+str(j)+str(k))
terminaciones.append(str(500))
terminaciones.pop(0)


# Run the Spider
process = CrawlerProcess()
process.crawl(Diputados)
process.start()


2021-04-09 13:56:05 [scrapy.utils.log] INFO: Scrapy 2.4.1 started (bot: scrapybot)
2021-04-09 13:56:05 [scrapy.utils.log] INFO: Versions: lxml 4.6.2.0, libxml2 2.9.5, cssselect 1.1.0, parsel 1.6.0, w3lib 1.22.0, Twisted 21.2.0, Python 3.8.2 (tags/v3.8.2:7b3ab59, Feb 25 2020, 23:03:10) [MSC v.1916 64 bit (AMD64)], pyOpenSSL 20.0.1 (OpenSSL 1.1.1j  16 Feb 2021), cryptography 3.4.6, Platform Windows-10-10.0.19041-SP0
2021-04-09 13:56:05 [scrapy.utils.log] DEBUG: Using reactor: twisted.internet.selectreactor.SelectReactor
2021-04-09 13:56:05 [scrapy.crawler] INFO: Overridden settings:
{}
2021-04-09 13:56:05 [scrapy.extensions.telnet] INFO: Telnet Password: 15753ad0cef8f77c
2021-04-09 13:56:06 [scrapy.middleware] INFO: Enabled extensions:
['scrapy.extensions.corestats.CoreStats',
 'scrapy.extensions.telnet.TelnetConsole',
 'scrapy.extensions.logstats.LogStats']
2021-04-09 13:56:07 [scrapy.middleware] INFO: Enabled downloader middlewares:
['scrapy.downloadermiddlewares.httpauth.HttpAuthMiddl

2021-04-09 13:56:10 [scrapy.core.engine] DEBUG: Crawled (200) <GET http://sitl.diputados.gob.mx/LXIV_leg/votaciones_diputados_xperiodonplxiv.php?dipt=013> (referer: http://sitl.diputados.gob.mx/LXIV_leg/curricula.php?dipt=013)
2021-04-09 13:56:10 [scrapy.core.engine] DEBUG: Crawled (200) <GET http://sitl.diputados.gob.mx/LXIV_leg/asistencias_diputados_xperiodonplxiv.php?dipt=020> (referer: http://sitl.diputados.gob.mx/LXIV_leg/curricula.php?dipt=020)
2021-04-09 13:56:10 [scrapy.core.engine] DEBUG: Crawled (200) <GET http://sitl.diputados.gob.mx/LXIV_leg/asistencias_diputados_xperiodonplxiv.php?dipt=013> (referer: http://sitl.diputados.gob.mx/LXIV_leg/curricula.php?dipt=013)
2021-04-09 13:56:10 [scrapy.core.engine] DEBUG: Crawled (200) <GET http://sitl.diputados.gob.mx/LXIV_leg/votaciones_diputados_xperiodonplxiv.php?dipt=003> (referer: http://sitl.diputados.gob.mx/LXIV_leg/curricula.php?dipt=003)
2021-04-09 13:56:10 [scrapy.core.engine] DEBUG: Crawled (200) <GET http://sitl.diputados.g

2021-04-09 13:56:20 [scrapy.core.engine] DEBUG: Crawled (200) <GET http://sitl.diputados.gob.mx/LXIV_leg/votaciones_por_pernplxiv.php?iddipt=16&pert=15> (referer: http://sitl.diputados.gob.mx/LXIV_leg/votaciones_diputados_xperiodonplxiv.php?dipt=016)
2021-04-09 13:56:20 [scrapy.core.engine] DEBUG: Crawled (200) <GET http://sitl.diputados.gob.mx/LXIV_leg/votaciones_por_pernplxiv.php?iddipt=16&pert=14> (referer: http://sitl.diputados.gob.mx/LXIV_leg/votaciones_diputados_xperiodonplxiv.php?dipt=016)
2021-04-09 13:56:22 [scrapy.core.engine] DEBUG: Crawled (200) <GET http://sitl.diputados.gob.mx/LXIV_leg/votaciones_por_pernplxiv.php?iddipt=16&pert=16> (referer: http://sitl.diputados.gob.mx/LXIV_leg/votaciones_diputados_xperiodonplxiv.php?dipt=016)
2021-04-09 13:56:26 [scrapy.core.engine] DEBUG: Crawled (200) <GET http://sitl.diputados.gob.mx/LXIV_leg/votaciones_por_pernplxiv.php?iddipt=16&pert=8> (referer: http://sitl.diputados.gob.mx/LXIV_leg/votaciones_diputados_xperiodonplxiv.php?dipt=01

2021-04-09 13:56:35 [scrapy.core.engine] DEBUG: Crawled (200) <GET http://sitl.diputados.gob.mx/LXIV_leg/votaciones_por_pernplxiv.php?iddipt=17&pert=7> (referer: http://sitl.diputados.gob.mx/LXIV_leg/votaciones_diputados_xperiodonplxiv.php?dipt=017)
2021-04-09 13:56:35 [scrapy.core.engine] DEBUG: Crawled (200) <GET http://sitl.diputados.gob.mx/LXIV_leg/votaciones_por_pernplxiv.php?iddipt=17&pert=6> (referer: http://sitl.diputados.gob.mx/LXIV_leg/votaciones_diputados_xperiodonplxiv.php?dipt=017)
2021-04-09 13:56:35 [scrapy.core.engine] DEBUG: Crawled (200) <GET http://sitl.diputados.gob.mx/LXIV_leg/votaciones_por_pernplxiv.php?iddipt=17&pert=4> (referer: http://sitl.diputados.gob.mx/LXIV_leg/votaciones_diputados_xperiodonplxiv.php?dipt=017)
2021-04-09 13:56:38 [scrapy.core.engine] DEBUG: Crawled (200) <GET http://sitl.diputados.gob.mx/LXIV_leg/votaciones_por_pernplxiv.php?iddipt=17&pert=1> (referer: http://sitl.diputados.gob.mx/LXIV_leg/votaciones_diputados_xperiodonplxiv.php?dipt=017)


2021-04-09 13:56:39 [scrapy.core.engine] DEBUG: Crawled (200) <GET http://sitl.diputados.gob.mx/LXIV_leg/votaciones_por_pernplxiv.php?iddipt=18&pert=6> (referer: http://sitl.diputados.gob.mx/LXIV_leg/votaciones_diputados_xperiodonplxiv.php?dipt=018)
2021-04-09 13:56:39 [scrapy.core.engine] DEBUG: Crawled (200) <GET http://sitl.diputados.gob.mx/LXIV_leg/votaciones_por_pernplxiv.php?iddipt=18&pert=8> (referer: http://sitl.diputados.gob.mx/LXIV_leg/votaciones_diputados_xperiodonplxiv.php?dipt=018)
2021-04-09 13:56:39 [scrapy.core.engine] DEBUG: Crawled (200) <GET http://sitl.diputados.gob.mx/LXIV_leg/votaciones_por_pernplxiv.php?iddipt=18&pert=3> (referer: http://sitl.diputados.gob.mx/LXIV_leg/votaciones_diputados_xperiodonplxiv.php?dipt=018)
2021-04-09 13:56:39 [scrapy.core.engine] DEBUG: Crawled (200) <GET http://sitl.diputados.gob.mx/LXIV_leg/votaciones_por_pernplxiv.php?iddipt=18&pert=7> (referer: http://sitl.diputados.gob.mx/LXIV_leg/votaciones_diputados_xperiodonplxiv.php?dipt=018)


...

2021-04-09 14:39:52 [scrapy.core.engine] DEBUG: Crawled (200) <GET http://sitl.diputados.gob.mx/LXIV_leg/asistencias_por_pernplxiv.php?iddipt=498&pert=8> (referer: http://sitl.diputados.gob.mx/LXIV_leg/asistencias_diputados_xperiodonplxiv.php?dipt=498)
2021-04-09 14:39:52 [scrapy.core.engine] DEBUG: Crawled (200) <GET http://sitl.diputados.gob.mx/LXIV_leg/asistencias_por_pernplxiv.php?iddipt=498&pert=7> (referer: http://sitl.diputados.gob.mx/LXIV_leg/asistencias_diputados_xperiodonplxiv.php?dipt=498)
2021-04-09 14:39:52 [scrapy.core.engine] DEBUG: Crawled (200) <GET http://sitl.diputados.gob.mx/LXIV_leg/asistencias_por_pernplxiv.php?iddipt=498&pert=6> (referer: http://sitl.diputados.gob.mx/LXIV_leg/asistencias_diputados_xperiodonplxiv.php?dipt=498)
2021-04-09 14:39:55 [scrapy.core.engine] DEBUG: Crawled (200) <GET http://sitl.diputados.gob.mx/LXIV_leg/asistencias_por_pernplxiv.php?iddipt=498&pert=3> (referer: http://sitl.diputados.gob.mx/LXIV_leg/asistencias_diputados_xperiodonplxiv.ph

2021-04-09 14:40:01 [scrapy.core.engine] DEBUG: Crawled (200) <GET http://sitl.diputados.gob.mx/LXIV_leg/votaciones_por_pernplxiv.php?iddipt=489&pert=3> (referer: http://sitl.diputados.gob.mx/LXIV_leg/votaciones_diputados_xperiodonplxiv.php?dipt=489)
2021-04-09 14:40:01 [scrapy.core.engine] DEBUG: Crawled (200) <GET http://sitl.diputados.gob.mx/LXIV_leg/votaciones_por_pernplxiv.php?iddipt=489&pert=1> (referer: http://sitl.diputados.gob.mx/LXIV_leg/votaciones_diputados_xperiodonplxiv.php?dipt=489)
2021-04-09 14:40:01 [scrapy.core.engine] DEBUG: Crawled (200) <GET http://sitl.diputados.gob.mx/LXIV_leg/asistencias_por_pernplxiv.php?iddipt=486&pert=13> (referer: http://sitl.diputados.gob.mx/LXIV_leg/asistencias_diputados_xperiodonplxiv.php?dipt=486)
2021-04-09 14:40:01 [scrapy.core.engine] DEBUG: Crawled (200) <GET http://sitl.diputados.gob.mx/LXIV_leg/asistencias_por_pernplxiv.php?iddipt=486&pert=11> (referer: http://sitl.diputados.gob.mx/LXIV_leg/asistencias_diputados_xperiodonplxiv.php?

2021-04-09 14:40:07 [scrapy.core.engine] DEBUG: Crawled (200) <GET http://sitl.diputados.gob.mx/LXIV_leg/asistencias_por_pernplxiv.php?iddipt=490&pert=3> (referer: http://sitl.diputados.gob.mx/LXIV_leg/asistencias_diputados_xperiodonplxiv.php?dipt=490)
2021-04-09 14:40:07 [scrapy.core.engine] DEBUG: Crawled (200) <GET http://sitl.diputados.gob.mx/LXIV_leg/asistencias_diputados_xperiodonplxiv.php?dipt=499> (referer: http://sitl.diputados.gob.mx/LXIV_leg/curricula.php?dipt=499)
2021-04-09 14:40:07 [scrapy.core.engine] DEBUG: Crawled (200) <GET http://sitl.diputados.gob.mx/LXIV_leg/votaciones_diputados_xperiodonplxiv.php?dipt=496> (referer: http://sitl.diputados.gob.mx/LXIV_leg/curricula.php?dipt=496)
2021-04-09 14:40:07 [scrapy.core.engine] DEBUG: Crawled (200) <GET http://sitl.diputados.gob.mx/LXIV_leg/asistencias_por_pernplxiv.php?iddipt=490&pert=7> (referer: http://sitl.diputados.gob.mx/LXIV_leg/asistencias_diputados_xperiodonplxiv.php?dipt=490)
2021-04-09 14:40:07 [scrapy.core.engine

2021-04-09 14:40:13 [scrapy.core.engine] DEBUG: Crawled (200) <GET http://sitl.diputados.gob.mx/LXIV_leg/asistencias_por_pernplxiv.php?iddipt=499&pert=14> (referer: http://sitl.diputados.gob.mx/LXIV_leg/asistencias_diputados_xperiodonplxiv.php?dipt=499)
2021-04-09 14:40:13 [scrapy.core.engine] DEBUG: Crawled (200) <GET http://sitl.diputados.gob.mx/LXIV_leg/asistencias_por_pernplxiv.php?iddipt=499&pert=13> (referer: http://sitl.diputados.gob.mx/LXIV_leg/asistencias_diputados_xperiodonplxiv.php?dipt=499)
2021-04-09 14:40:13 [scrapy.core.engine] DEBUG: Crawled (200) <GET http://sitl.diputados.gob.mx/LXIV_leg/asistencias_por_pernplxiv.php?iddipt=492&pert=16> (referer: http://sitl.diputados.gob.mx/LXIV_leg/asistencias_diputados_xperiodonplxiv.php?dipt=492)
2021-04-09 14:40:13 [scrapy.core.engine] DEBUG: Crawled (200) <GET http://sitl.diputados.gob.mx/LXIV_leg/votaciones_por_pernplxiv.php?iddipt=492&pert=18> (referer: http://sitl.diputados.gob.mx/LXIV_leg/votaciones_diputados_xperiodonplxiv.

2021-04-09 14:40:24 [scrapy.core.engine] DEBUG: Crawled (200) <GET http://sitl.diputados.gob.mx/LXIV_leg/votaciones_por_pernplxiv.php?iddipt=492&pert=11> (referer: http://sitl.diputados.gob.mx/LXIV_leg/votaciones_diputados_xperiodonplxiv.php?dipt=492)
2021-04-09 14:40:24 [scrapy.core.engine] DEBUG: Crawled (200) <GET http://sitl.diputados.gob.mx/LXIV_leg/votaciones_por_pernplxiv.php?iddipt=492&pert=9> (referer: http://sitl.diputados.gob.mx/LXIV_leg/votaciones_diputados_xperiodonplxiv.php?dipt=492)
2021-04-09 14:40:24 [scrapy.core.engine] DEBUG: Crawled (200) <GET http://sitl.diputados.gob.mx/LXIV_leg/votaciones_por_pernplxiv.php?iddipt=492&pert=16> (referer: http://sitl.diputados.gob.mx/LXIV_leg/votaciones_diputados_xperiodonplxiv.php?dipt=492)
2021-04-09 14:40:24 [scrapy.core.engine] DEBUG: Crawled (200) <GET http://sitl.diputados.gob.mx/LXIV_leg/votaciones_por_pernplxiv.php?iddipt=492&pert=8> (referer: http://sitl.diputados.gob.mx/LXIV_leg/votaciones_diputados_xperiodonplxiv.php?dipt

In [8]:
list_of_dipus = [value for value in dipus.values()]

In [9]:
list_of_votos = [value for value in por_votaciones.values()]

In [10]:
with open('diputados_64.json', 'a') as f:
            json.dump(list_of_dipus, f, indent=4, ensure_ascii=False) # antes dipus

In [11]:
with open('votaciones_64.json', 'a') as f:
            json.dump(list_of_votos, f, indent=4, ensure_ascii=False)

In [10]:
for key, value in dipus.items():
    print('\n',key, ' : \n\n', value)


 ELBALORENATORRESDIAZ  : 

 {'CURP': 'ELBALORENATORRESDIAZ', 'Nombre': 'Elba Lorena Torres Díaz', 'TipoElección': 'Mayoría Relativa', 'Entidad': 'Aguascalientes ', 'Partido': 'PT', 'Distrito': '2 H-278 ', 'Correo': 'elba.torres@diputados.gob.mx ', 'Extensión': '62100 ', 'Onomástico': '15-marzo-1977 ', 'Suplente': 'Haydeé Hernández Muñoz', 'Comisiones': [' Salud (Secretaría) '], 'Último grado de estudios': 'Licenciatura', 'Asistencias': 130, 'votos': 610}

 FRANCISCOJAVIERLUEVANONUNEZ  : 

 {'CURP': 'FRANCISCOJAVIERLUEVANONUNEZ', 'Nombre': 'Francisco Javier Luévano Núñez', 'TipoElección': 'Mayoría Relativa', 'Entidad': 'Aguascalientes ', 'Partido': 'PAN', 'Distrito': '1 H-249 ', 'Correo': 'francisco.luevano@diputados.gob.mx ', 'Extensión': '59907 ', 'Onomástico': '1-julio-1979 ', 'Suplente': 'Gustavo Armendariz Viramontes', 'Comisiones': [' Asuntos Migratorios  ', ' Comunicaciones y Transportes (Secretaría) ', ' Presupuesto y Cuenta Pública  ', ' Alemania (Vicepresidencia) ', ' Bielorr

In [13]:
for key, value in por_votaciones.items():
    print('\n',key,': ')
    for curp, posi in value.items():
        print('\n',curp, ': ', posi)


 DECRETO POR EL QUE SE ADICIONA UN PÁRRAFO AL ARTÍCULO 1° DE LA LEY DE ADQUISICIONES ARRENDAMIENTOS Y SERVICIOS DEL SECTOR PÚBLICO (EN LO GENERAL Y EN LO PARTICULAR)  : 

 ID_voto :  AUPAA1AASSPGP

 Nombre_Votación :  DECRETO POR EL QUE SE ADICIONA UN PÁRRAFO AL ARTÍCULO 1° DE LA LEY DE ADQUISICIONES ARRENDAMIENTOS Y SERVICIOS DEL SECTOR PÚBLICO (EN LO GENERAL Y EN LO PARTICULAR) 

 MARIOISMAELMORENOGIL :  Ausente

 HECTORRENECRUZAPARICIO :  A favor

 IRASEMADELCARMENBUENFILDIAZ :  Ausente

 ARMANDOGONZALEZESCOTO :  A favor

 MIGUELANGELJAUREGUIMONTESDEOCA :  A favor

 GERARDOFERNANDEZNORONA :  A favor

 ERIKAVANESSADELCASTILLOIBARRA :  A favor

 CLAUDIALOPEZRAYON :  A favor

 CARLOSENRIQUEMARTINEZAKE :  A favor

 ANARUTHGARCIAGRANDE :  Ausente

 ARMANDOREYESLEDESMA :  Ausente

 FRANCISCOJAVIERLUEVANONUNEZ :  Ausente

 ELBALORENATORRESDIAZ :  A favor

 MARTHAELISAGONZALEZESTRADA :  En contra

 JESUSSALVADORMINORMORA :  A favor

 SOCORROIRMAANDAZOLAGOMEZ :  A favor

 ERIKISAACMORALESEL

 FRINNEAZUARAYARZABAL :  Ausente

 MARIANARODRIGUEZMIERYTERAN :  A favor

 RUBENIGNACIOMOREIRAVALDEZ :  A favor

 PEDROPABLOTREVINOVILLARREAL :  Ausente

 CARLOSPAVONCAMPOS :  A favor

 ANTONIOORTEGAMARTINEZ :  En contra

 PILARLOZANOMACDONALD :  En contra

 MA.DEJESUSGARCIAGUARDADO :  A favor

 MIRIAMCITLALLYPEREZMACKINTOSH :  A favor

 ALBERTOVILLAVILLEGAS :  A favor

 MARIATERESALOPEZPEREZ :  A favor

 SEBASTIANAGUILERABRENES :  A favor

 CARLOSALBERTOPUENTESALAS :  A favor

 FRANCISCOELIZONDOGARRIDO :  A favor

 CECILIAANUNCIACIONPATRONLAVIADA :  En contra

 LENINNELSONCAMPOSCORDOVA :  Ausente

 MARIAALEMANMUNOZCASTILLO :  A favor

 MARIALUISAVELOZSILVA :  Ausente

 DIEGOEDUARDODELBOSQUEVILLARREAL :  A favor

 MARTINACAZAREZYANEZ :  Ausente

 CUAUHTLIFERNANDOBADILLOMORENO :  A favor

 JUANISRAELRAMOSRUIZ :  A favor

 OSCARRAFAELNOVELLAMACIAS :  A favor

 LIDIANALLELYVARGASHERNANDEZ :  A favor

 MIROSLAVASANCHEZGALVAN :  A favor

 NORMAGUELSALDIVAR :  Ausente

 MIGUELANGELCHICOHERRE


 ARMANDOJAVIERZERTUCHEZUANI :  Ausente

 JOSEDELALUZSOSASALINAS :  Ausente

 FLORATANIACRUZSANTOS :  A favor

 PAOLATENORIOADAME :  A favor

 MARIANADUNYASKAGARCIAROJAS :  A favor

 JOSEELIASLIXAABIMERHI :  Ausente

 MARIAESTERALONZOMORALES :  Ausente

 JESUSCARLOSVIDALPENICHE :  A favor

 BONIFACIOAGUILARLINDA :  Ausente

 VALENTINREYESLOPEZ :  A favor

 CARMENMEDELPALMA :  Ausente

 ELEUTERIOARRIETASANCHEZ :  A favor

 RAFAELHERNANDEZVILLALPANDO :  Ausente

 JESUSGUZMANAVILES :  Ausente

 CARMENMORAGARCIA :  A favor

 EULALIOJUANRIOSFARARONI :  A favor

 DULCEMARIACORINAVILLEGASGUARNEROS :  Ausente

 JAIMEHUMBERTOPEREZBERNABE :  A favor

 RODRIGOCALDERONSALAS :  A favor

 CLAUDIATELLOESPINOSA :  A favor

 JUANMARTINEZFLORES :  A favor

 SAMUELHERRERACHAVEZ :  A favor

 LYNDIANAELIZABETHBUGARINCORTES :  Ausente

 JUANJOSECANULPEREZ :  Ausente

 MADELEINEBONNAFOUXALCARAZ :  A favor

 JOSERIGOBERTOMARESAGUILAR :  A favor

 ERNESTOGUILLERMORUFFOAPPEL :  Ausente

 PATRICIATERRAZASBACA : 


 HILDELISAGONZALEZMORALES :  A favor

 ADRIANALOZANORODRIGUEZ :  A favor

 MANUELRODRIGUEZGONZALEZ :  A favor

 HECTORJOELVILLEGASGONZALEZ :  A favor

 MARIOALBERTORAMOSTAMEZ :  A favor

 ARMANDOJAVIERZERTUCHEZUANI :  Ausente

 JOSEDELALUZSOSASALINAS :  Ausente

 FLORATANIACRUZSANTOS :  A favor

 PAOLATENORIOADAME :  A favor

 MARIANADUNYASKAGARCIAROJAS :  A favor

 JOSEELIASLIXAABIMERHI :  Ausente

 MARIAESTERALONZOMORALES :  Ausente

 JESUSCARLOSVIDALPENICHE :  A favor

 BONIFACIOAGUILARLINDA :  Ausente

 VALENTINREYESLOPEZ :  A favor

 CARMENMEDELPALMA :  Ausente

 ELEUTERIOARRIETASANCHEZ :  A favor

 RAFAELHERNANDEZVILLALPANDO :  Ausente

 JESUSGUZMANAVILES :  Ausente

 CARMENMORAGARCIA :  A favor

 EULALIOJUANRIOSFARARONI :  A favor

 DULCEMARIACORINAVILLEGASGUARNEROS :  Ausente

 JAIMEHUMBERTOPEREZBERNABE :  A favor

 RODRIGOCALDERONSALAS :  A favor

 CLAUDIATELLOESPINOSA :  A favor

 JUANMARTINEZFLORES :  A favor

 SAMUELHERRERACHAVEZ :  A favor

 LYNDIANAELIZABETHBUGARINCORTES

 CASIMIROZAMORAVALDEZ :  Ausente

 MERARYVILLEGASSANCHEZ :  Ausente

 MANUELDEJESUSBALDENEBROARREDONDO :  A favor

 JOSERICARDODELSOLESTRADA :  A favor

 MILDREDCONCEPCIONAVILAVERA :  A favor

 ADRIANAPAULINATEISSIERZAVALA :  A favor

 MARCELINORIVERAHERNANDEZ :  A favor

 OSCARBAUTISTAVILLEGAS :  A favor

 JOSERICARDOGALLARDOCARDONA :  A favor

 JESUSDELOSANGELESPOOLMOO :  Ausente

 CARMENPATRICIAPALMAOLVERA :  A favor

 GREGORIOEFRAINESPADASMENDEZ :  Ausente

 LAURAPATRICIAAVALOSMAGANA :  A favor

 OLGAPATRICIASOSARUIZ :  A favor

 RICARDOGARCIAESCALANTE :  Ausente

 VICENTEJAVIERVERASTEGUIOSTOS :  Ausente

 JOSESALVADORROSASQUINTANILLA :  Ausente

 ERASMOGONZALEZROBLEDO :  Ausente

 OLGAJULIANAELIZONDOGUERRA :  A favor

 RICARDODELAPENAMARSHALL :  Ausente

 CARLOSJAVIERLAMARQUECANO :  Ausente

 TERESABURELOCORTAZAR :  Ausente

 MARIAWENDYBRICENOZULOAGA :  A favor

 RUBENTERANAGUILA :  A favor

 HERIBERTOMARCELOAGUILARCASTILLO :  A favor

 ESTELANUNEZALVAREZ :  A favor

 LORENIAIVETH

...

 NORMAGUELSALDIVAR :  En contra

 EDELMIROSANTIAGOSANTOSDIAZ :  Ausente

 TEOFILOMANUELGARCIACORPUS :  A favor

 MARIADELROSARIOGUZMANAVILES :  Ausente

 DULCEALEJANDRAGARCIAMORLAN :  En contra

 JUANORTIZGUARNEROS :  En contra

 HECTORYUNESLANDA :  En contra

 DULCEMARIASAURIRIANCHO :  En contra

 MANUELLIMONHERNANDEZ :  Ausente

 SORAYAPEREZMUNGUIA :  En contra

 PABLOGUILLERMOANGULOBRICENO :  Ausente

 ANILUINGRAMVALLINES :  Ausente

 NORMAAZUCENARODRIGUEZZAMORA :  En contra

 DULCEMARIAMENDEZDELALUZDAUZON :  En contra

 ANTONIANATIVIDADDIAZJIMENEZ :  Ausente

 JOSEDELCARMENGOMEZQUEJ :  Ausente

 CARLOSALBERTOVALENZUELAGONZALEZ :  Ausente

 CARLOSALBERTOMORALESVAZQUEZ :  En contra

 PATRICIADELCARMENDELACRUZDELUCIO :  A favor

 VIRGINIAMERINOGARCIA :  A favor

 GRACIELAZAVALETASANCHEZ :  Ausente

 ANAPATRICIAPERALTADELAPENA :  Ausente

 EMETERIACLAUDIAMARTINEZAGUILAR :  A favor

 MANUELGOMEZVENTURA :  A favor

 LUISJAVIERALEGRESALAZAR :  Ausente

 IRANSANTIAGOMANUEL :  A favor

 JUL

 MARCOANTONIOCARBAJALMIRANDA :  A favor

 ERIKAMARIANAROSASURIBE :  En contra

 MARTHAANGELICAZAMUDIOMACIAS :  En contra

 MARCOANTONIOGOMEZALCANTAR :  En contra

 JORGEEUGENIORUSSOSALIDO :  En contra

 MARIALIBIERGONZALEZANAYA :  En contra

 LUCINDASANDOVALSOBERANES :  A favor

 JOSEISABELTREJOREYES :  En contra

 JACQUELINAMARTINEZJUAREZ :  En contra

 FERNANDOTORRESGRACIANO :  En contra

 ISABELMARGARITAGUERRAVILLARREAL :  En contra

 SILVIAGUADALUPEGARZAGALVAN :  En contra

 NOHEMIALEMANHERNANDEZ :  A favor

 MARTHAPATRICIARAMIREZLUCERO :  A favor

 XAVIERAZUARAZUNIGA :  En contra

 EFRAINROCHAVEGA :  A favor

 VICTORMANUELPEREZDIAZ :  Ausente

 FRANCISCOJAVIERGUZMANDELATORRE :  A favor

 CARMINAYADIRAREGALADOMARDUENO :  A favor

 KATIAALEJANDRACASTILLOLOZANO :  A favor

 RAULGRACIAGUZMAN :  Ausente

 MARCOSAGUILARVEGA :  En contra

 MARIAMARCELATORRESPEIMBERT :  Ausente

 SYLVIAVIOLETAGARFIASCEDILLO :  En contra

 ANTONIOORTEGAMARTINEZ :  En contra

 FRIDAALEJANDRAESPARZAMARQUEZ :

 MAIELLAMARTHAGABRIELAGOMEZMALDONADO :  En contra

 HECTORGUILLERMODEJESUSJIMENEZYMENESES :  A favor

 ROSALINDADOMINGUEZFLORES :  A favor

 BEATRIZSILVIAROBLESGUTIERREZ :  A favor

 ANAPAOLALOPEZBIRLAIN :  Ausente

 FELIPEFERNANDOMACIASOLVERA :  En contra

 BEATRIZDOMINGAPEREZLOPEZ :  A favor

 INESPARRAJUAREZ :  A favor

 MARIADELCARMENBAUTISTAPELAEZ :  A favor

 DANIELGUTIERREZGUTIERREZ :  A favor

 BENJAMINSAULHUERTACORONA :  A favor

 ALEJANDROCARVAJALHIDALGO :  Ausente

 JULIETAKRISTALVENCESVALENCIA :  A favor

 ADRIANAPAULINATEISSIERZAVALA :  En contra

 JESUSFERNANDOGARCIAHERNANDEZ :  En contra

 MA.GUADALUPEALMAGUERPARDO :  Ausente

 JOSEFINASALAZARBAEZ :  En contra

 OLEGARIACARRAZCOMACIAS :  A favor

 NANCYYADIRASANTIAGOMARCOS :  A favor

 MA.SARAROCHAMEDINA :  En contra

 CASIMIROZAMORAVALDEZ :  A favor

 MERARYVILLEGASSANCHEZ :  A favor

 MANUELDEJESUSBALDENEBROARREDONDO :  En contra

 JOSERICARDODELSOLESTRADA :  A favor

 MILDREDCONCEPCIONAVILAVERA :  A favor

 MARCELINOR

 ESMERALDADELOSANGELESMORENOMEDINA :  A favor

 ROBERTOANGELDOMINGUEZRODRIGUEZ :  A favor

 KARLAYURITZIALMAZANBURGOS :  A favor

 CRUZJUVENALROASANCHEZ :  En contra

 ARTUROROBERTOHERNANDEZTAPIA :  Ausente

 LUISENRIQUEMARTINEZVENTURA :  En contra

 JOSELUISMONTALVOLUNA :  En contra

 CESARAGUSTINHERNANDEZPEREZ :  A favor

 VICENTEALBERTOONOFREVAZQUEZ :  A favor

 JUANPABLOSANCHEZRODRIGUEZ :  A favor

 ESTEBANBARAJASBARAJAS :  A favor

 FELICIANOFLORESANGUIANO :  A favor

 ARMANDOTEJEDACID :  En contra

 MARYCARMENBERNALMARTINEZ :  En contra

 MARCOANTONIOREYESCOLIN :  A favor

 NANCYCLAUDIARESENDIZHERNANDEZ :  En contra

 MARIADELOSANGELESHUERTADELRIO :  A favor

 OSCARGONZALEZYANEZ :  Ausente

 DELFINO(DECESO)LOPEZAPARICIO :  A favor

 GRACIELASANCHEZORTIZ :  A favor

 JUANANGELBAUTISTABRAVO :  A favor

 MARTHAROBLESORTIZ :  A favor

 YOLANDAGUERREROBARRERA :  A favor

 ALEJANDROMOJICATOLEDO :  A favor

 IGNACIOBENJAMINCAMPOSEQUIHUA :  A favor

 IVANARTUROPEREZNEGRONRUIZ :  A favor


KeyboardInterrupt: 

In [18]:
limpiaText("Ma. Guadalupe Loredo Gonzáles\n\t\t\t\t\t\n\n\n ")

'Ma. Guadalupe Loredo Gonzáles'

In [9]:
"Dip. Martha Elisa González Estrada (LICENCIA)".replace(' (LICENCIA)', '')

'Dip. Martha Elisa González Estrada'